In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from pathlib import Path
import json

import lightgbm as lgb
from sklearn.model_selection import GroupKFold

print("Lightgbm version:", lgb.__version__)

import optuna
from optuna.visualization import (
    plot_edf
    , plot_optimization_history
    , plot_parallel_coordinate
    , plot_param_importances
    , plot_slice
)

print("Optuna version:", optuna.__version__)

# local modules
import sys
sys.path.append("../src")
from preproc import process_train_data

Lightgbm version: 4.5.0


/Users/mavillan/Library/Caches/pypoetry/virtualenvs/mcts-strength-variants-E8z0EJ47-py3.10/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


Optuna version: 4.0.0


***
### load and preprocess data

In [2]:
# define some paths
path_raw = Path("../data/raw")
path_processed = Path("../data/processed")
path_results = Path("../data/results")

# load data
df_train = pd.read_csv(path_raw / "train.csv")
df_test = pd.read_csv(path_raw / "test.csv")

df_train

Id GameRulesetName                                        agent1  \
0            0             00Y        MCTS-ProgressiveHistory-0.1-MAST-false   
1            1             00Y        MCTS-ProgressiveHistory-0.1-MAST-false   
2            2             00Y         MCTS-ProgressiveHistory-0.1-MAST-true   
3            3             00Y         MCTS-ProgressiveHistory-0.1-MAST-true   
4            4             00Y         MCTS-ProgressiveHistory-0.1-MAST-true   
...        ...             ...                                           ...   
233229  233229     Zuz_Mel_7x7        MCTS-UCB1Tuned-1.41421356237-NST-false   
233230  233230     Zuz_Mel_7x7  MCTS-UCB1Tuned-1.41421356237-Random200-false   
233231  233231     Zuz_Mel_7x7  MCTS-UCB1Tuned-1.41421356237-Random200-false   
233232  233232     Zuz_Mel_7x7  MCTS-UCB1Tuned-1.41421356237-Random200-false   
233233  233233     Zuz_Mel_7x7   MCTS-UCB1Tuned-1.41421356237-Random200-true   

                                                   agent2  Properties  Format  \
0             MCTS-ProgressiveHistory-0.6-Random200-false           1       1   
1                             MCTS-UCB1GRAVE-0.6-NST-true           1       1   
2                                 MCTS-UCB1-0.1-NST-false           1       1   
3                                 MCTS-UCB1-0.6-NST-false           1       1   
4                  MCTS-UCB1GRAVE-1.41421356237-NST-false           1       1   
...                                                   ...         ...     ...   
233229  MCTS-ProgressiveHistory-1.41421356237-Random20...           1       1   
233230                           MCTS-UCB1-0.6-MAST-false           1       1   
233231             MCTS-UCB1GRAVE-1.41421356237-NST-false           1       1   
233232              MCTS-UCB1GRAVE-1.41421356237-NST-true           1       1   
233233                      MCTS-UCB1Tuned-0.6-MAST-false           1       1   

        Time  Discrete  Realtime  Turns  ...  DoLudeme  Trigger  \
0          1         1         0      1  ...         0        1   
1          1         1         0      1  ...         0        1   
2          1         1         0      1  ...         0        1   
3          1         1         0      1  ...         0        1   
4          1         1         0      1  ...         0        1   
...      ...       ...       ...    ...  ...       ...      ...   
233229     1         1         0      1  ...         0        0   
233230     1         1         0      1  ...         0        0   
233231     1         1         0      1  ...         0        0   
233232     1         1         0      1  ...         0        0   
233233     1         1         0      1  ...         0        0   

        PlayoutsPerSecond  MovesPerSecond  \
0                  298.07        18877.17   
1                  298.07        18877.17   
2                  298.07        18877.17   
3                  298.07        18877.17   
4                  298.07        18877.17   
...                   ...             ...   
233229             157.52       157174.58   
233230             157.52       157174.58   
233231             157.52       157174.58   
233232             157.52       157174.58   
233233             157.52       157174.58   

                                             EnglishRules  \
0       Goal: Connect all three edge colors with a sin...   
1       Goal: Connect all three edge colors with a sin...   
2       Goal: Connect all three edge colors with a sin...   
3       Goal: Connect all three edge colors with a sin...   
4       Goal: Connect all three edge colors with a sin...   
...                                                   ...   
233229  7x7 board. 24 pieces per player. Pieces begin ...   
233230  7x7 board. 24 pieces per player. Pieces begin ...   
233231  7x7 board. 24 pieces per player. Pieces begin ...   
233232  7x7 board. 24 pieces per player. Pieces begin ...   
233233  7x7 board. 24 pieces per player. Pieces begin ...   


In [3]:
# Call the function
df_train, numerical_cols, categorical_cols, encoder, scaler = process_train_data(
    df_train,
    scale=False
)

# Print the results
print("Numerical Columns:", len(numerical_cols))
print("Categorical Columns:", len(categorical_cols))

number of all nan cols:  18
number of constant cols:  198
Numerical Columns: 588
Categorical Columns: 10


***
### optimization



In [4]:
# Define the number of folds for cross-validation
num_folds = 5

# Shuffle the train dataset
df_train = df_train.sample(frac=1, random_state=2112).reset_index(drop=True)

# Define the column for stratified or group k-fold
groups_col = 'GameRulesetName'
gkf = GroupKFold(n_splits=num_folds)
split_list = list(gkf.split(df_train, groups=df_train[groups_col]))

In [5]:
def train_and_score(numerical_cols, categorical_cols):

    # Define the parameters
    params = {
        'objective': "regression",
        'metric': 'rmse',
        'boosting_type': 'gbdt',
        'num_leaves': 31,
        'max_depth': 10,
        'learning_rate': 0.1,
        'reg_alpha': 1e-1,
        'reg_lambda': 1e-1,
        'feature_fraction': 0.8,
        'verbose': -1,
        'seed': 2112,
    }

    target = 'utility_agent1'
    oof_scores = []

    # Perform cross-validation
    for _, (train_index, val_index) in enumerate(split_list, 1):
        # Split the data
        X_train, X_val = df_train.iloc[train_index], df_train.iloc[val_index]
        y_train, y_val = X_train[target], X_val[target]
        
        # Create LightGBM datasets
        train_data = lgb.Dataset(
            data=X_train[numerical_cols + categorical_cols],
            label=y_train,
            categorical_feature=categorical_cols,
            free_raw_data=True
        )
        val_data = lgb.Dataset(
            data=X_val[numerical_cols + categorical_cols],
            label=y_val,
            categorical_feature=categorical_cols,
            free_raw_data=True
        )

        # Train the model
        model = lgb.train(
            params,
            train_data,
            num_boost_round=1000,
            valid_sets=[val_data],
        )

        # predict on validation set
        y_pred = model.predict(X_val[numerical_cols + categorical_cols])
        y_pred = np.clip(y_pred, -1, 1)
        
        # Compute RMSE on scaled values
        rmse = np.sqrt(np.mean((y_pred - y_val) ** 2))
        oof_scores.append(rmse)

    return np.mean(oof_scores)


In [6]:
def objective(trial):
    # Feature selection
    selected_numerical = [col for col in numerical_cols if trial.suggest_int(f'use_{col}', 0, 1) == 1]
    selected_categorical = [col for col in categorical_cols if trial.suggest_int(f'use_{col}', 0, 1) == 1]
        
    # Call the train_and_score function with selected features
    score = train_and_score(selected_numerical, selected_categorical)
    
    return score

In [7]:
do_optimize = True
timeout = 3600 * 8

study = optuna.create_study(
    study_name="optuna_lgbm",
    direction='minimize',
    storage='sqlite:///optuna_lgbm.db',
    load_if_exists=True,
)

if do_optimize:

    # manually enqueueing a trial with all features
    # trial_params = {f'use_{col}': 1 for col in numerical_cols + categorical_cols}
    # study.enqueue_trial(trial_params)

    study.optimize(
        objective, 
        n_trials=100000, 
        timeout=timeout,
        n_jobs=1, 
        gc_after_trial=True,
    ) 

[I 2024-10-17 12:40:12,716] Using an existing study with name 'optuna_lgbm' instead of creating a new one.
[I 2024-10-17 12:41:20,513] Trial 844 finished with value: 0.43795537841547433 and parameters: {'use_Stochastic': 1, 'use_Asymmetric': 0, 'use_AsymmetricForces': 0, 'use_AsymmetricPiecesType': 1, 'use_PlayersWithDirections': 0, 'use_Cooperation': 1, 'use_Team': 0, 'use_Shape': 1, 'use_SquareShape': 0, 'use_HexShape': 0, 'use_TriangleShape': 0, 'use_DiamondShape': 0, 'use_RectangleShape': 0, 'use_SpiralShape': 1, 'use_CircleShape': 1, 'use_StarShape': 1, 'use_SquarePyramidalShape': 1, 'use_RegularShape': 0, 'use_PolygonShape': 1, 'use_Tiling': 1, 'use_SquareTiling': 0, 'use_HexTiling': 1, 'use_TriangleTiling': 1, 'use_SemiRegularTiling': 0, 'use_MorrisTiling': 1, 'use_CircleTiling': 1, 'use_ConcentricTiling': 0, 'use_SpiralTiling': 1, 'use_AlquerqueTiling': 1, 'use_MancalaBoard': 1, 'use_MancalaStores': 1, 'use_MancalaTwoRows': 0, 'use_MancalaThreeRows': 0, 'use_MancalaFourRows': 1

In [8]:
study.trials_dataframe().sort_values("value", ascending=True).head(20)

number     value             datetime_start          datetime_complete  \
1072    1072  0.429055 2024-10-17 16:21:55.816167 2024-10-17 16:22:59.055196   
1074    1074  0.429055 2024-10-17 16:24:02.499448 2024-10-17 16:25:06.361633   
1075    1075  0.429055 2024-10-17 16:25:06.530164 2024-10-17 16:26:09.763364   
1076    1076  0.429055 2024-10-17 16:26:09.933077 2024-10-17 16:27:12.700557   
1023    1023  0.429543 2024-10-17 15:33:54.751272 2024-10-17 15:34:52.423342   
1040    1040  0.429661 2024-10-17 15:50:15.613936 2024-10-17 15:51:13.300528   
953      953  0.429937 2024-10-17 14:24:15.582160 2024-10-17 14:25:16.188456   
1031    1031  0.430050 2024-10-17 15:41:37.448381 2024-10-17 15:42:34.628334   
1018    1018  0.430107 2024-10-17 15:29:10.472883 2024-10-17 15:30:06.517935   
1081    1081  0.430123 2024-10-17 16:31:26.647004 2024-10-17 16:32:24.311372   
1320    1320  0.430212 2024-10-17 20:26:24.284070 2024-10-17 20:27:22.325110   
1186    1186  0.430212 2024-10-17 18:15:09.555583 2024-10-17 18:16:09.753151   
1185    1185  0.430212 2024-10-17 18:14:08.591899 2024-10-17 18:15:09.377316   
1183    1183  0.430212 2024-10-17 18:12:07.580561 2024-10-17 18:13:08.640778   
1237    1237  0.430212 2024-10-17 19:05:37.793966 2024-10-17 19:06:36.644770   
1199    1199  0.430212 2024-10-17 18:28:12.144495 2024-10-17 18:29:12.742489   
1188    1188  0.430212 2024-10-17 18:17:09.025194 2024-10-17 18:18:12.907665   
1240    1240  0.430212 2024-10-17 19:08:33.570918 2024-10-17 19:09:31.936389   
1242    1242  0.430212 2024-10-17 19:10:30.301923 2024-10-17 19:11:28.134242   
1178    1178  0.430212 2024-10-17 18:07:08.379649 2024-10-17 18:08:07.809140   

                   duration  params_use_Absolute  \
1072 0 days 00:01:03.239029                    1   
1074 0 days 00:01:03.862185                    1   
1075 0 days 00:01:03.233200                    1   
1076 0 days 00:01:02.767480                    1   
1023 0 days 00:00:57.672070                    1   
1040 0 days 00:00:57.686592                    1   
953  0 days 00:01:00.606296                    1   
1031 0 days 00:00:57.179953                    1   
1018 0 days 00:00:56.045052                    1   
1081 0 days 00:00:57.664368                    1   
1320 0 days 00:00:58.041040                    1   
1186 0 days 00:01:00.197568                    1   
1185 0 days 00:01:00.785417                    1   
1183 0 days 00:01:01.060217                    1   
1237 0 days 00:00:58.850804                    1   
1199 0 days 00:01:00.597994                    1   
1188 0 days 00:01:03.882471                    1   
1240 0 days 00:00:58.365471                    1   
1242 0 days 00:00:57.832319                    1   
1178 0 days 00:00:59.429491                    1   

      params_use_AbsoluteDirections  params_use_AddDecision  \
1072                              0                       0   
1074                              0                       0   
1075                              0                       0   
1076                              0                       0   
1023                              0                       0   
1040                              0                       0   
953                               0                       0   
1031                              0                       0   
1018                              0                       0   
1081                              0                       0   
1320                              0                       0   
1186                              0                       0   
1185                              0                       0   
1183                              0                       0   
1237                              0                       0   
1199                              0                       0   
1188                              0                       0   
1240                              0                       0   
1242                              0

In [9]:
# Get the selected features from the best trial
best_params = study.best_trial.params

# Filter numerical and categorical features
selected_numerical = [col for col in numerical_cols if best_params.get(f'use_{col}', 0) == 1]
selected_categorical = [col for col in categorical_cols if best_params.get(f'use_{col}', 0) == 1]

# Combine selected features
selected_features = selected_numerical + selected_categorical

print("Selected features:")
print("len(numerical): ", len(selected_numerical), "/", len(numerical_cols))
print("len(categorical): ", len(selected_categorical), "/", len(categorical_cols))
print("len(selected_features): ", len(selected_features), "/", len(numerical_cols) + len(categorical_cols))


# Save selected features to a file
selected_features_dict = {
    "numerical": selected_numerical,
    "categorical": selected_categorical
}
with open('select_optuna_lgbm.json', 'w') as f:
    json.dump(selected_features_dict, f, indent=2)

print("Selected features have been saved to 'select_optuna_lgbm.json'")

Selected features:
len(numerical):  281 / 588
len(categorical):  6 / 10
len(selected_features):  287 / 598
Selected features have been saved to 'select_optuna_lgbm.json'


***